# Thermal fin

## Problem statement

We consider the problem of designing a thermal fin to effectively remove heat from a surface. The two-dimensional fin, shown in Figure below, consists of a vertical central post and four horizontal subfins; the fin conducts heat from a prescribed uniform flux source at the root, $\Gamma_{\text {root }}$, through the large-surface-area subfins to surrounding flowing air. The fin is characterized by a five-component parameter vector, or input, $\mu_{=}\left(\mu_1, \mu_2, \ldots, \mu_5\right)$, where $\mu_i=k^i, i=1, \ldots, 4$, and $\mu_5=\mathrm{Bi} ; \mu$ may take on any value in a specified design set $D \subset \mathbb{R}^5$.

![ROOT:fin2d 4 mesh](ROOT:fin2d-4-mesh.png)

Here $k^i$ is the thermal conductivity of the ith subfin (normalized relative to the post conductivity $k^0 \equiv 1$ ); and $\mathrm{Bi}$ is the Biot number, a nondimensional heat transfer coefficient reflecting convective transport to the air at the fin surfaces (larger $\mathrm{Bi}$ means better heat transfer). For example, suppose we choose a thermal fin with $k^1=0.4, k^2=0.6, k^3=0.8, k^4=1.2$, and $\mathrm{Bi}=0.1$; for this particular configuration $\mu=\{0.4,0.6,0.8,1.2,0.1\}$, which corresponds to a single point in the set of all possible configurations D (the parameter or design set). The post is of width unity and height four; the subfins are of fixed thickness $t=0.25$ and length $L=2.5$.
We are interested in the design of this thermal fin, and we thus need to look at certain outputs or cost-functionals of the temperature as a function of $\mu$. We choose for our output $T_{\text {root }}$, the average steady-state temperature of the fin root normalized by the prescribed heat flux into the fin root. The particular output chosen relates directly to the cooling efficiency of the fin lower values of $T_{\text {root }}$ imply better thermal performance. The steadystate temperature distribution within the fin, $u(\mu)$, is governed by the elliptic partial differential equation

$$
\rho_i C_i \frac{\partial u^i}{\partial t} -k^i \Delta u^i=0 \text { in } \Omega^i, i=0, \ldots, 4,
$$
where $\Delta$ is the Laplacian operator, and $u_i$ refers to the restriction of $u$ to $\Omega^i$.
Here $\Omega^i$ is the region of the fin with conductivity $k^i, i=0, \ldots, 4$ and volumetric heat capacity $(\rho C)_i, i=0, \cdots, 4$: $\Omega^0$ is thus the central post, and $\Omega^i, i=1, \ldots, 4$, corresponds to the four subfins.
The entire fin domain is denoted $\Omega\left(\bar{\Omega}=\cup_{i=0}^4 \bar{\Omega}^i\right)$; the boundary $\Omega$ is denoted $\Gamma$. We must also ensure continuity of temperature and heat flux at the conductivity discontinuity interfaces $\Gamma_{\text {int }}^i \equiv \partial \Omega^0 \cap \partial \Omega^i, i=1, \ldots, 4$, where $\partial \Omega^i$ denotes the boundary of $\Omega^i$, we have on $\Gamma_{\text {int }}^i i=1, \ldots, 4$ :

$$
\begin{aligned}
u^0 & =u^i \\
-\left(\nabla u^0 \cdot n^i\right) & =-k^i\left(\nabla u^i \cdot n^i\right)
\end{aligned}
$$
here $n^i$ is the outward normal on $\partial \Omega^i$. Finally, we introduce a Neumann flux boundary condition on the fin root

$$
-\left(\nabla u^0 \cdot n^0\right)=-1 \text { on } \Gamma_{\text {root }},
$$
which models the heat source; and a Robin boundary condition

$$
-k^i\left(\nabla u^i \cdot n^i\right)=\operatorname{Bi} u^i \text { on } \Gamma_{e x t}^i, i=0, \ldots, 4,
$$
which models the convective heat losses. Here $\Gamma_{\text {ext }}^i$ is that part of the boundary of $\Omega^i$ exposed to the flowing fluid; note that $\cup_{i=0}^4 \Gamma_{e x t}^i=\Gamma \backslash \Gamma_{\text {root }}$. The average temperature at the root, $T_{\text {root }}(\mu)$, can then be expressed as $\ell^O(u(\mu))$, where

$$
\ell^O(v)=\int_{\Gamma_{\text {root }}} v
$$
## Implementation

First, we initialize the {feelpp} environment and set the working directory.


In [ ]:
import feelpp
from feelpp.project import laplacian
import json
import os

d = os.getcwd()
print(f"directory={d}")
e = feelpp.Environment(['fin'], config=feelpp.localRepository("."))



Next, we set the configuration file for the simulation and load the specifications from a JSON file.


In [ ]:
feelpp.Environment.setConfigFile(f"{d}/src/cases/laplacian/fin/fin4/fin2d.cfg")
# Reading the JSON file
data = laplacian.loadSpecs(f"{d}/src/cases/laplacian/fin/fin2d.json")
print(data)


Now, we create a Laplacian object, set the specifications, and run the simulation.


In [ ]:
lap = laplacian.get(dim=2, order=1)
lap.setSpecs(data)
lap.initialize()


After running the simulation, we convert the results to a Pandas DataFrame and set the 'time' column as the index for easy data manipulation.


In the next block, we plot the mean temperature values at the fin root and the exterior using Plotly.


Lastly, we plot the heat flux values at the fin root and the exterior.


In [ ]:
import numpy as np
from petsc4py import PETSc

Fq=[]
for i,mat in enumerate(['Gamma_root']):
    print(f"mat={mat}")
    Fq.append(lap.assembleFlux(markers=[mat],coeffs=1))



In [ ]:
from feelpp.project.forms import *
Aq=[]
for i,mat in enumerate(['Post', 'Fin_1', 'Fin_2', 'Fin_3', 'Fin_4']):
    print(f"mat={mat}")
    C=np.array([[1,0],[0,1]])
    Aq.append(lap.assembleGradGrad(markers=[mat],coeffs=C))
for i,mat in enumerate(['Gamma_ext']):
    print(f"mat={mat}")
    Aq.append(lap.assembleMass(markers=[mat],coeffs=1))

a=form2(test=lap.Xh(),trial=lap.Xh())
a = sum([aq for aq in Aq],start=a)
f = form1(test=lap.Xh())
f = sum([fq for fq in Fq],start=f)
a.solve(solution=lap.u(),rhs=f)
lap.exportResults()
meas=lap.measures()


In [ ]:
import pandas as pd
df = pd.DataFrame(meas)
df.set_index('time', inplace=True)
print(df.to_markdown())

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=df.index, y=df["flux_Gamma_root"], mode='lines', name='Flux_{Gamma Root}'))
fig.add_trace(go.Scatter(
    x=df.index, y=df["flux_Gamma_ext"], mode='markers', name='Flux_{Gamma Ext}'))
fig.update_layout(title='Heat Flux', xaxis_title='time', yaxis_title='Flux')
fig.show()


In [ ]:
import plotly.graph_objects as go
import numpy as np

fig = go.Figure()
fig.add_trace(go.Scatter(x=df.index, y=df["mean_Gamma_root"], mode='lines', name='T_{Gamma Root}'))
fig.add_trace(go.Scatter(x=df.index, y=df["mean_Gamma_ext"], mode='markers', name='T_{Gamma Ext}'))
fig.add_trace(go.Scatter(x=df.index, y=df["min"], mode='markers', name='min T'))
fig.add_trace(go.Scatter(x=df.index, y=df["max"], mode='markers', name='max T'))
fig.update_layout(title='Temperature', xaxis_title='time', yaxis_title='T')
fig.show()


In [1]:
import feelpp
from feelpp.project import laplacian
from feelpp.project.forms import *
import numpy as np
import json
import os

d=os.getcwd()
print(f"directory={d}")
e=feelpp.Environment(['lap'],config=feelpp.localRepository("."))



directory=/nvme0/prudhomm/Devel/feelpp-project
[ Starting Feel++ ] application lap version 0.1 date 2023-Nov-27
 . lap files are stored in /nvme0/prudhomm/Devel/feelpp-project/feelppdb/./np_1
 .. logfiles :/nvme0/prudhomm/Devel/feelpp-project/feelppdb/./np_1/logs


In [2]:
feelpp.Environment.setConfigFile(f"{d}/src/cases/laplacian/fin/fin4/fin2d.cfg")
data = laplacian.loadSpecs(f"{d}/src/cases/laplacian/fin/fin2d.json")
lap=laplacian.get(dim=2,order=1)
lap.setSpecs(data)
lap.initialize()

def decompose():
    Fq=[]
    for i,mat in enumerate(['Gamma_root']):
        Fq.append(lap.assembleFlux(markers=[mat],coeffs=1))
    Aq=[]
    for i,mat in enumerate(['Post', 'Fin_1', 'Fin_2', 'Fin_3', 'Fin_4']):
        C=np.array([[1,0],[0,1]])
        Aq.append(lap.assembleGradGrad(markers=[mat],coeffs=C))
    for i,mat in enumerate(['Gamma_ext']):
        Aq.append(lap.assembleMass(markers=[mat],coeffs=1))
    return Aq,Fq

Aq,Fq=decompose()

mus = [1, 1, 1, 1, 1]
def atheta0(mu): return 1
def atheta1(mu): return mu[0]
def atheta2(mu): return mu[1]
def atheta3(mu): return mu[2]
def atheta4(mu): return mu[3]
def atheta5(mu): return mu[4]
a_thetas=[atheta0,atheta1,atheta2,atheta3,atheta4,atheta5]
def ftheta0(mu): return 1
f_thetas=[ftheta0]

def a(mu):
    return sum( (theta(mu) * aq for theta, aq in zip(a_thetas, Aq)),start=form2(test=lap.Xh(),trial=lap.Xh()))
def f(mu):
    return sum( (theta(mu) * fq for theta, fq in zip(f_thetas, Fq)),start=form1(test=lap.Xh()))

def log_random_sample(bounds, num_samples=1):
    # bounds is a list of tuples (a, b) for each dimension
    log_bounds = [(np.log(a), np.log(b)) for a, b in bounds]
    samples = [np.exp(np.random.uniform(log_a, log_b, num_samples)) for log_a, log_b in log_bounds]
    return np.array(samples).T  # Transpose to get samples in shape (num_samples, dimensions)

def log_equidistributed_sample(bounds, num_samples=1):
    # bounds is a list of tuples (a, b) for each dimension
    log_bounds = [(np.log(a), np.log(b)) for a, b in bounds]
    samples = [np.exp(np.linspace(log_a,log_b,num_samples )) for log_a, log_b in log_bounds]
    return np.array(samples).T  # Transpose to get samples in shape (num_samples, dimensions)

def solve(mu,index=0):
    u = lap.Xh().element()
    fmu=f(mu)
    a(mu).solve(solution=u,rhs=fmu)
    lap.exportResults(index,u)
    return u,fmu(u)


Reading /nvme0/prudhomm/Devel/feelpp-project/src/cases/laplacian/fin/fin4/fin2d.cfg...
[loadMesh] Loading mesh in format geo+msh: "/nvme0/prudhomm/Devel/feelpp-project/src/cases/laplacian/fin/fin4/../fin.geo"
[loadMesh] Use default geo desc: /nvme0/prudhomm/Devel/feelpp-project/src/cases/laplacian/fin/fin4/../fin.geo 0.025 
Info    : Reading 'fin.geo'...
fin = 1
fin = 2
fin = 3
fin = 4
Fin number 9 1 
Fin number 11 2 
Fin number 13 3 
Fin number 15 4 
boundary number 1 = 3
boundary number 3 = 8
boundary number 4 = 10
boundary number 5 = 14
boundary number 6 = 16
boundary number 7 = 20
boundary number 8 = 22
boundary number 9 = 24
boundary number 10 = 26
boundary number 11 = 27
boundary number 12 = 28
boundary number 13 = 29
boundary number 14 = 30
boundary number 15 = 31
boundary number 16 = 32
boundary number 17 = 33
boundary number 18 = 34
boundary number 19 = 35
boundary number 20 = 36
boundary number 21 = 37
boundary number 22 = 38
boundary number 23 = 39
boundary number 24 = 40
bo

In [3]:
mu_bar=[1.5,1.5,1.5,1.5,.1]
a_bar = a(mu_bar)

sampling=log_equidistributed_sample([(1.5,1.5),(.01,1)], num_samples=20)

for i,sample in enumerate(sampling):
    mu=[sample[0],sample[0],sample[0],sample[0],sample[1]]
    u,s=solve(mu,index=i)
    print(f"s({mu})={s}")

s([1.5, 1.5, 1.5, 1.5, 0.010000000000000004])=3.984477262337503
s([1.5, 1.5, 1.5, 1.5, 0.01274274985703134])=3.516516471396401
s([1.5, 1.5, 1.5, 1.5, 0.01623776739188723])=3.137250154378895
s([1.5, 1.5, 1.5, 1.5, 0.020691380811147905])=2.8264472521560946
s([1.5, 1.5, 1.5, 1.5, 0.026366508987303586])=2.5683346546855277
s([1.5, 1.5, 1.5, 1.5, 0.03359818286283783])=2.35063419555815
s([1.5, 1.5, 1.5, 1.5, 0.04281332398719396])=2.1637885799352987
s([1.5, 1.5, 1.5, 1.5, 0.0545559478116852])=2.0003513534249207
s([1.5, 1.5, 1.5, 1.5, 0.06951927961775607])=1.8545258372721938
s([1.5, 1.5, 1.5, 1.5, 0.0885866790410083])=1.721836352991251
s([1.5, 1.5, 1.5, 1.5, 0.11288378916846892])=1.5989057050629305
s([1.5, 1.5, 1.5, 1.5, 0.1438449888287663])=1.4833031771084824
s([1.5, 1.5, 1.5, 1.5, 0.18329807108324367])=1.373424484489259
s([1.5, 1.5, 1.5, 1.5, 0.23357214690901223])=1.268372498019528
s([1.5, 1.5, 1.5, 1.5, 0.29763514416313186])=1.1678227424288272
s([1.5, 1.5, 1.5, 1.5, 0.3792690190732249])=1.07

In [4]:
meas=lap.measures()
print(f"meas={meas}")
print(f"mus={mus}")
print(f"sampling={sampling[:,1]}")

meas={'flux_Gamma_ext': [-0.7311499327153672, -0.7332489513654616, -0.7358467451896823, -0.7390415111917135, -0.7429409793196903, -0.7476584953337583, -0.7533065274380009, -0.7599872990760528, -0.7677808148567822, -0.7767313854681633, -0.7868346424715112, -0.7980275529568688, -0.8101837014875045, -0.8231150547761364, -0.836580047929388, -0.85029687721696, -0.8639607240966021, -0.8772638649377866, -0.8899174481639089, -0.9016728468223784], 'flux_Gamma_root': [0.9988804947939476, 0.9987424447534613, 0.998572211766105, 0.9983632365186209, 0.9981079094540763, 0.997797508847982, 0.9974222087757125, 0.996971199440273, 0.9964329539527688, 0.995795649596911, 0.995047712724872, 0.9941784180945851, 0.9931784519832385, 0.9920403532725741, 0.9907587730449393, 0.9893305250593286, 0.9877544249202022, 0.9860309407165282, 0.98416171996925, 0.9821491203325099], 'max': [3.9877685742383897, 3.5201827628671216, 3.1413771306845266, 2.831137384471317, 2.573709622597696, 2.356837380141638, 2.170987382008088,

In [5]:
import pandas as pd
df = pd.DataFrame(meas)
print(df.to_markdown())

|    |   flux_Gamma_ext |   flux_Gamma_root |      max |      mean |   mean_Fin_1 |   mean_Fin_2 |   mean_Fin_3 |   mean_Fin_4 |   mean_Gamma_ext |   mean_Gamma_root |   mean_Post |         min |   quantity_Fin_1 |   quantity_Fin_2 |   quantity_Fin_3 |   quantity_Fin_4 |   quantity_Gamma_ext |   quantity_Gamma_root |   quantity_Post |   time |   totalFlux |   totalQuantity |
|---:|-----------------:|------------------:|---------:|----------:|-------------:|-------------:|-------------:|-------------:|-----------------:|------------------:|------------:|------------:|-----------------:|-----------------:|-----------------:|-----------------:|---------------------:|----------------------:|----------------:|-------:|------------:|----------------:|
|  0 |        -0.73115  |          0.99888  | 3.98777  | 2.19911   |    2.57369   |   2.02272    |   1.6837     |  1.51534     |        2.0202    |          3.98448  |    2.49351  | 1.42241     |        3.21711   |       2.5284     |      2.104

In [6]:
import plotly.graph_objects as go
import numpy as np

fig = go.Figure()
fig.add_trace(go.Scatter(
    x=sampling[:,1], y=df["mean_Gamma_root"], mode='lines+markers', name='Mean_{Gamma Root}'))
# fig.add_trace(go.Scatter(
#     x=sampling[:,1], y=df["flux_Gamma_ext"], mode='markers', name='Flux_{Gamma Ext}'))
fig.update_layout(title='Mean Temperature', xaxis_title='mu', yaxis_title='Temperature')
fig.show()

In [16]:
from xvfbwrapper import Xvfb
vdisplay = Xvfb()
vdisplay.start()

import pyvista as pv
import os

pv.set_jupyter_backend('panel')
def pv_get_mesh(mesh_path,time):
    reader = pv.get_reader(mesh_path)
    reader.set_active_time_value(time)
    mesh = reader.read()
    return mesh

def pv_plot(mesh, field, clim=None, cmap='viridis', cpos='xy', show_scalar_bar=True, show_edges=True):
    mesh.plot(scalars=field, clim=clim, cmap=cmap, cpos=cpos, show_scalar_bar=show_scalar_bar, show_edges=show_edges)

def myplots(dim=2, field="u", time=0, factor=1, cmap='viridis'):
    mesh = pv_get_mesh(f"exports/ensightgold/lap/lap.case",time)
    pv_plot(mesh, field)

/tmp/ipykernel_1919186/2788094939.py:8: PyVistaDeprecationWarning:

`panel` backend is deprecated and is planned for future removal.



In [19]:
myplots(dim=2,factor=0.5,time=10)

VTKRenderWindowSynchronized(vtkXOpenGLRenderWindow, color_mappers=[LinearColorMapper(id='103...], orientation_widget=True, sizing_mode='stretch_width')